## Load all companies from DB

In [1]:
# Get all companies from REST API
import requests
import json
from collections import defaultdict
    
resp = json.loads(requests.get(f"http://localhost:8000/api/v1/company/").text)
    
if resp['code'] != 200:
    print(resp['message'])
else:
    data = resp['data']
    dict_of_lists_for_companies = defaultdict(list)
    for idx, company_obj in enumerate(data):
        dict_of_lists_for_companies[company_obj['cik']].append(company_obj)
 
list_of_companies = []        
for k,v in dict_of_lists_for_companies.items():
    list_of_companies.append(v)
    

In [2]:
len(list_of_companies)

275

In [3]:
from collections import defaultdict

# Get length of sections to be able to see distribution

list_of_results = []
for list_curr_company in list_of_companies:
    company_results = {}
    for curr_dict in list_curr_company:
        q_to_metadata = defaultdict(list)
        for quarter in curr_dict['quarters']:
            for metadata_dict in quarter['metadata']:
                if metadata_dict['risk_section']:
                    metadata_dict['risk_section_len'] = len(metadata_dict['risk_section'].split())
                else:
                    metadata_dict['risk_section_len'] = 0
                    
                if metadata_dict['mda_section']:
                    metadata_dict['mda_section_len'] = len(metadata_dict['mda_section'].split())
                else:
                    metadata_dict['mda_section_len'] = 0
                    
                if metadata_dict['qqd_section']:
                    metadata_dict['qqd_section_len'] = len(metadata_dict['qqd_section'].split())
                else:
                    metadata_dict['qqd_section_len'] = 0
                
                copy_metadata_dict = metadata_dict.copy()
                copy_metadata_dict['filing_date'] = metadata_dict['filing_date']
                copy_metadata_dict['period_of_report'] = metadata_dict['period_of_report']
                del copy_metadata_dict['qqd_section']
                del copy_metadata_dict['risk_section']
                del copy_metadata_dict['mda_section']
                q_to_metadata[quarter['q']].append(copy_metadata_dict)
            
        company_results['cik'] = curr_dict['cik']
        company_results[curr_dict['year']] = q_to_metadata
    
    list_of_results.append(company_results)

## Analysis on the data

In [4]:
print(f"Number of companies is {len(list_of_results)}")

Number of companies is 275


In [5]:
import plotly.express as px
from collections import defaultdict
import pandas as pd

def get_df_plotly(use_data='all'): # possible type: 'all', 'year'
    if use_data == 'all':
        list_for_df = []
        for company in list_of_results:
            for year in range(2017, 2022):
                for q in range(1,5):
                    if not company.get(year,None):
                        continue
                    curr_q = company[year].get(q, None)
                    
                    if not curr_q:
                        continue
                    for dict_metadata in curr_q:
                        if dict_metadata['risk_section_len'] > 0:
                            list_for_df.append({'section_type': 'risk', 'len_text': dict_metadata['risk_section_len'],
                                                'cik':company['cik'], 'year':year, 'q': q, 'filing_type': dict_metadata['type'], 
                                                'filing_date': dict_metadata['filing_date'], 'period_of_report': dict_metadata['period_of_report']})
                        if dict_metadata['mda_section_len'] > 0:
                            list_for_df.append({'section_type': 'mda', 'len_text': dict_metadata['mda_section_len'],
                                                'cik':company['cik'], 'year':year, 'q': q, 'filing_type': dict_metadata['type'],
                                                'filing_date': dict_metadata['filing_date'], 'period_of_report': dict_metadata['period_of_report']})
                        if dict_metadata['qqd_section_len'] > 0:
                            list_for_df.append({'section_type': 'qqd', 'len_text': dict_metadata['qqd_section_len'],
                                                'cik':company['cik'], 'year':year, 'q': q, 'filing_type': dict_metadata['type'],
                                                'filing_date': dict_metadata['filing_date'], 'period_of_report': dict_metadata['period_of_report']})
        
    return pd.DataFrame(list_for_df)
    

In [6]:
df = get_df_plotly()

In [7]:
fig = px.histogram(df, x="len_text",color="section_type", marginal="rug",
                   hover_data=df.columns, title="All filings from 2017 to 2022 by section type")
fig.show()

In [8]:
fig = px.histogram(df, x="len_text",color="filing_type", marginal="rug",
                   hover_data=df.columns, title="All filings from 2017 to 2022 by type of filing")
fig.show()

In [31]:
fig = px.histogram(df.loc[df['section_type'] == 'risk'], x="len_text", color="filing_type", marginal="rug",
                   hover_data=df.columns, title="Risk sections from 2017 to 2022 by filing type")
fig.show()

## Criterias to use company in the data
- If data is not missing for a sequence of 3 or more for risk and mda.

In [9]:
# Leave only 10K, 10Q, 10KA, 10QA
df_cleaned = df.loc[df['filing_type'].isin(['10K', '10Q'])]

In [10]:
df_cleaned.loc[df_cleaned['filing_type'] == '10K']

section_type  len_text      cik  year  q filing_type  \
0             risk      2148    34088  2017  1         10K   
1              mda        47    34088  2017  1         10K   
2              qqd        78    34088  2017  1         10K   
6             risk      2468    34088  2018  1         10K   
7              mda        48    34088  2018  1         10K   
...            ...       ...      ...   ... ..         ...   
11155          mda      3184  1718405  2020  1         10K   
11156          qqd        97  1718405  2020  1         10K   
11163         risk     12363  1718405  2021  1         10K   
11164          mda     11325  1718405  2021  1         10K   
11165          qqd        48  1718405  2021  1         10K   

               filing_date     period_of_report  
0      2017-02-22T00:00:00  2016-12-31T00:00:00  
1      2017-02-22T00:00:00  2016-12-31T00:00:00  
2      2017-02-22T00:00:00  2016-12-31T00:00:00  
6      2018-02-28T00:00:00  2017-12-31T00:00:00  
7      2018-02-28T00:00:00  2017-12-31T00:00:00  
...                    ...                  ...  
11155  2020-03-12T00:00:00  2019-12-31T00:00:00  
11156  2020-03-12T00:00:00  2019-12-31T00:00:00  
11163  2021-03-24T00:00:00  2020-12-31T00:00:00  
11164  2021-03-24T00:00:00  2020-12-31T00:00:00  
11165  2021-03-24T00:00:00  2020-12-31T00:00:00  

[3711 rows x 8 columns]

In [11]:
# Create new dfs based on section type
df_risk_only = df_cleaned.loc[df_cleaned['section_type'] == "risk"]
df_mda_only = df_cleaned.loc[df_cleaned['section_type'] == "mda"]

In [12]:
from collections import defaultdict

def get_missing_data_companies_df(df):
    dict_results = defaultdict(list)
    list_ciks = list(set(df['cik']))
    for cik in list_ciks:
        cik_df = df.loc[df['cik'] == cik]
        for year in range(2017,2022):
            year_df = cik_df.loc[cik_df['year'] == year]
            q_series = year_df['q'].values
            for q in range(1,5):
                if q not in q_series:
                    dict_results[cik].append(f"{year}_{q}")
                    
    return dict_results

In [13]:
missing_mda = get_missing_data_companies_df(df_mda_only)
missing_risk = get_missing_data_companies_df(df_risk_only)

In [14]:
print(f"MDA df number of companies: {len(set(df_mda_only['cik']))}")
print(f"MDA number of companies with missing data: {len(missing_mda)}")
print(f"RISK df number of companies: {len(set(df_risk_only['cik']))}")
print(f"RISK number of companies with missing data: {len(missing_risk)}")

MDA df number of companies: 275
MDA number of companies with missing data: 69
RISK df number of companies: 275
RISK number of companies with missing data: 98


In [15]:
def get_companies_to_remove(missing_dict_section, consecutive_count=3):
    # remove companies that have consecutive missing filings e.g 2017_1, 2017_2, 2017_3
    dict_of_cik_consecutives = {}
    for cik, list_year_q in missing_dict_section.items():
        curr_consecutive_count = 1
        best_consecutive_count = 1
        for i in range(len(list_year_q) - 1):
            curr_year, curr_q = [int(x) for x in list_year_q[i].split('_')]
            next_year, next_q = [int(x) for x in list_year_q[i+1].split('_')]
            
            
            if curr_q + 1 == next_q and curr_q < 4 and curr_year == next_year:
                curr_consecutive_count += 1
                if curr_consecutive_count > best_consecutive_count:
                    best_consecutive_count = curr_consecutive_count
            elif curr_q == 4 and curr_year + 1 == next_year and next_q == 1:
                curr_consecutive_count += 1
                if curr_consecutive_count > best_consecutive_count:
                    best_consecutive_count = curr_consecutive_count
            else:
                if curr_consecutive_count > best_consecutive_count:
                    best_consecutive_count = curr_consecutive_count
                curr_consecutive_count = 1
        
        if best_consecutive_count >= consecutive_count:
            dict_of_cik_consecutives[cik] = best_consecutive_count
            
    return dict_of_cik_consecutives

In [16]:
# Check duplicated ciks in the two dicts for statistics and remove all from original DF

dict_mda_consecutives = get_companies_to_remove(missing_mda, 3)
dict_risk_consecutives = get_companies_to_remove(missing_risk, 3)

In [17]:
count_duplicated = 0
for cik, count_consecutives in dict_mda_consecutives.items():
    if cik in dict_risk_consecutives:
        count_duplicated += 1

print(f"{count_duplicated/len(dict_mda_consecutives) * 100} % of MDA are also in Risk")       
print(f"Len of mda ciks {len(dict_mda_consecutives)}")
print(f"Len of risk ciks {len(dict_risk_consecutives)}")

100.0 % of MDA are also in Risk
Len of mda ciks 38
Len of risk ciks 66


## Remove companies that are not covering requirements from DF

In [18]:
# Remove the companies that lack consecutives

list_of_ciks_to_remove = list(set(list(dict_mda_consecutives.keys()) + list(dict_risk_consecutives.keys())))
df_cleaned = df_cleaned.loc[~df_cleaned['cik'].isin(list_of_ciks_to_remove)]

In [19]:
fig = px.histogram(df_cleaned, x="len_text",color="section_type", marginal="rug",
                   hover_data=df_cleaned.columns, title="Processed companies / All filings from 2017 to 2022 by section type")
fig.show()

In [94]:
fig = px.histogram(df_cleaned.loc[df_cleaned['section_type'] == 'risk'], x="len_text", color="filing_type", marginal="rug",
                   hover_data=df_cleaned.columns, title="Processed companies / Risk sections from 2017 to 2022 by filing type")
fig.show()

In [20]:
# Number of risk sections per company and number of mda section per company

def count_section_availablity(df):
    dict_of_res = {}
    list_ciks = list(set(df['cik']))
    for cik in list_ciks:
        cik_df = df.loc[df['cik'] == cik]
        dict_of_res[cik] = {'risk': cik_df['section_type'].value_counts().get('risk'), 'mda': cik_df['section_type'].value_counts().get('mda')}
    return dict_of_res


In [21]:
dict_count_section = count_section_availablity(df_cleaned)
dict_count_section

{799233: {'risk': 20, 'mda': 20},
 874499: {'risk': 20, 'mda': 20},
 1537028: {'risk': 20, 'mda': 20},
 1524741: {'risk': 20, 'mda': 20},
 10254: {'risk': 20, 'mda': 20},
 1449488: {'risk': 20, 'mda': 20},
 1602065: {'risk': 20, 'mda': 20},
 746515: {'risk': 20, 'mda': 20},
 1587732: {'risk': 20, 'mda': 20},
 100885: {'risk': 20, 'mda': 20},
 1038357: {'risk': 20, 'mda': 20},
 1171486: {'risk': 20, 'mda': 20},
 822818: {'risk': 20, 'mda': 20},
 1134115: {'risk': 20, 'mda': 20},
 56868: {'risk': 20, 'mda': 20},
 1362468: {'risk': 20, 'mda': 20},
 1060391: {'risk': 20, 'mda': 20},
 1522727: {'risk': 20, 'mda': 20},
 1587246: {'risk': 20, 'mda': 20},
 1308208: {'risk': 20, 'mda': 20},
 1255474: {'risk': 20, 'mda': 20},
 1512499: {'risk': 20, 'mda': 20},
 77877: {'risk': 20, 'mda': 20},
 1296445: {'risk': 20, 'mda': 20},
 1126975: {'risk': 20, 'mda': 20},
 1084991: {'risk': 20, 'mda': 20},
 1283140: {'risk': 20, 'mda': 20},
 1693256: {'risk': 19, 'mda': 19},
 351817: {'risk': 20, 'mda': 20

## Save dataframe to reuse 

In [22]:
df_cleaned.to_csv('D:/PythonProjects/MasterThesisResearch/Notebooks/data/df_text_cleaned.csv', index=False)

## Load the cleaned dataframe

In [23]:
import pandas as pd

df_cleaned = pd.read_csv('D:/PythonProjects/MasterThesisResearch/Notebooks/data/df_text_cleaned.csv')

In [24]:
print(f"Number of companies in the corpus: {len(set(df_cleaned['cik']))}")

Number of companies in the corpus: 209
